In [ ]:
import os
import cv2
import numpy as np 
import random
import math
import re
import shutil
import torch
import torchvision.transforms as T
import torchvision.transforms.functional as F

import albumentations as A
from torchvision import tv_tensors
from torchvision.transforms import v2, PILToTensor
from torchvision.transforms.functional import pil_to_tensor
from torchvision.io import read_image, write_jpeg
from torchvision.transforms.v2 import functional as F
from torchvision import tv_tensors

from PIL import Image


In [11]:
original_images = "/Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/images/original"
original_annotations = "/Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/annotation/original"
root_dir = "/Users/georgye/Documents/repos/ethz/dslab25"
base_dir_images = os.path.join(root_dir, "training/vacuum_pump/images/augmented")
base_dir_annotations = os.path.join(root_dir, "training/vacuum_pump/annotation/augmented")
out_base_images = os.path.join(root_dir, "training/vacuum_pump/images/augmented")
out_base_annotations = os.path.join(root_dir, "training/vacuum_pump/annotation/augmented")


In [12]:
N_STAGES = 8


# Copy orignals to augmented folder

In [19]:
shutil.copytree(original_images, base_dir_images)
shutil.copytree(original_annotations, base_dir_annotations)

'/Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/annotation/augmented'

# Rotate (images takes up to 2 mins)

In [ ]:

def rotate_image(image_path, out_image_path, out_annotation_path, angle):
	try:
		# Try using torchvision's read_image first
		try:
			image = read_image(image_path)
		except:
			# Fallback to PIL
			pil_image = Image.open(image_path).convert("RGB")
			image = PILToTensor()(pil_image)
		
		# Create rotation transformation with expand=True to avoid clipping
		transform = v2.Compose([
			v2.RandomRotation(degrees=(angle, angle), expand=True)
		])
		
		# Apply rotation to image
		rotated_image = transform(image)
		
		# Save rotated image
		write_jpeg(rotated_image, out_image_path, quality=95)
		
		# Create empty annotation file
		with open(out_annotation_path, 'w') as f:
			pass
			
		return True
	
	except Exception as e:
		print(f"Error processing {image_path}: {str(e)}")
		return False

stages = [f"stage_{i}" for i in N_STAGES]
for stage in stages:
	image_folder = os.path.join(base_dir_images, stage)
	out_image_folder = os.path.join(out_base_images, stage)
	out_annotation_folder = os.path.join(out_base_annotations, stage)
		
	# Create output directories if they don't exist
	os.makedirs(out_image_folder, exist_ok=True)
	os.makedirs(out_annotation_folder, exist_ok=True)

	# List only original images (skip already augmented ones)
	image_files = [f for f in os.listdir(image_folder) if f.lower().endswith((".jpg", ".jpeg", ".png")) and "_rot" not in f]

	for filename in image_files:
		image_path = os.path.join(image_folder, filename)
		base_filename = os.path.splitext(filename)[0]

		# Apply rotations at 20° increments from 20° to 360°
		for angle in range(20, 361, 20):
			out_image_filename = f"{base_filename}_rot{angle}.jpg"
			out_annotation_filename = f"{base_filename}_rot{angle}.txt"
			out_image_path = os.path.join(out_image_folder, out_image_filename)
			out_annotation_path = os.path.join(out_annotation_folder, out_annotation_filename)

			success = rotate_image(image_path, out_image_path, out_annotation_path, angle)

			if success:
				print(f"Processed {out_image_path} with rotation {angle}°")
			else:
				print(f"Failed to process {image_path} with rotation {angle}°")


Processed /Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/images/augmented/stage_0/stage_0_case_render_7_rot20.jpg with rotation 20°
Processed /Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/images/augmented/stage_0/stage_0_case_render_7_rot40.jpg with rotation 40°
Processed /Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/images/augmented/stage_0/stage_0_case_render_7_rot60.jpg with rotation 60°
Processed /Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/images/augmented/stage_0/stage_0_case_render_7_rot80.jpg with rotation 80°
Processed /Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/images/augmented/stage_0/stage_0_case_render_7_rot100.jpg with rotation 100°
Processed /Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/images/augmented/stage_0/stage_0_case_render_7_rot120.jpg with rotation 120°
Processed /Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/images/augmented/stag

# Rotate (labels correctly)

For this you need to label all 18 (360/20) rotations of render image 1, 2, 4

In [21]:
# Define the directories
BASE_LABELS_DIR = os.path.join(os.getcwd(), 'stage_0/labels/')

# Regular expressions for base and annotation files
base_pattern = re.compile(r'^stage_0_case_render_([124])_rot(\d+)\.txt$')
# For base we expect files: render_1, render_2, render_4.
# For the annotation files, we ignore any _perm_x part:
annot_pattern = re.compile(r'^stage_(\d+)(?:_perm_\d+)?_case_render_(\d+)_rot(\d+)\.txt$')

# Data structure to hold rotation-specific base info
# key: rotation (as string), value: dict with base, col_shift, row_shift, w, h
rotation_data = {}

# First, process the base folder and group by rotation
# We need to read render_1, render_2, and render_4 for each rotation
for fname in os.listdir(BASE_LABELS_DIR):
	match = base_pattern.match(fname)
	if not match:
		continue
	render_number, rot = match.groups()
	path = os.path.join(BASE_LABELS_DIR, fname)
	with open(path, 'r') as f:
		# Assume each file has one line like "0 x y w h"
		parts = f.read().strip().split()
		# Convert numeric values (skip the class since we'll use our own later)
		# Order: class, x, y, w, h
		try:
			_, x, y, w, h = parts
			x, y, w, h = float(x), float(y), float(w), float(h)
		except Exception as e:
			print(f"Error processing {fname}: {e}")
			continue

	if rot not in rotation_data:
		rotation_data[rot] = {}
	rotation_data[rot][f'render_{render_number}'] = (x, y, w, h)

# Now, compute for each rotation the base values, col_shift and row_shift
for rot, data in rotation_data.items():
	try:
		base_x, base_y, w, h = data['render_1']
		col_x, col_y, _, _ = data['render_2']
		row_x, row_y, _, _ = data['render_4']
	except KeyError:
		print(f"Missing base files for rotation {rot}. Skipping.")
		continue

	# Calculate shifts
	col_shift = (col_x - base_x, col_y - base_y)
	row_shift = (row_x - base_x, row_y - base_y)
	# Save computed values back
	rotation_data[rot] = {
		'base': (base_x, base_y),
		'col_shift': col_shift,
		'row_shift': row_shift,
		'w': w,
		'h': h
	}

# Function to compute new coordinates given render number and rotation data
def compute_new_coords(render_num, rot_info):
	# Render number is expected as integer in 1..9, mapping to a 3x3 grid.
	# grid_x: how many times to add col_shift, grid_y: how many times to add row_shift.
	render_num = int(render_num)
	grid_x = (render_num - 1) % 3
	grid_y = (render_num - 1) // 3
	base_x, base_y = rot_info['base']
	col_shift_x, col_shift_y = rot_info['col_shift']
	row_shift_x, row_shift_y = rot_info['row_shift']

	new_x = base_x + grid_x * col_shift_x + grid_y * row_shift_x
	new_y = base_y + grid_x * col_shift_y + grid_y * row_shift_y
	return new_x, new_y

# Now, process each annotation file in the annotations folder
for stage_folder in os.listdir(base_dir_annotations):
	stage_path = os.path.join(base_dir_annotations, stage_folder)
	if not os.path.isdir(stage_path):
		continue
	# Expect folder name like stage_0, stage_1, etc.
	stage_match = re.match(r'stage_(\d+)', stage_folder)
	if not stage_match:
		continue
	class_id = stage_match.group(1)

	# Process each file in the stage folder
	for fname in os.listdir(stage_path):
		annot_match = annot_pattern.match(fname)
		if not annot_match:
			continue
		file_class, render_str, rot = annot_match.groups()
		# We ignore file_class (it might be redundant with the folder) and any perm parts
		if rot not in rotation_data:
			print(f"Rotation {rot} not found in base data for file {fname}. Skipping.")
			continue
		rot_info = rotation_data[rot]
		# Compute new x and y using the grid derived from render number
		new_x, new_y = compute_new_coords(render_str, rot_info)
		w = rot_info['w']
		h = rot_info['h']

		# Create new annotation line (class from folder, then new_x, new_y, w, h)
		new_line = f"{class_id} {new_x} {new_y} {w} {h}\n"
		# Overwrite the file
		out_path = os.path.join(stage_path, fname)
		with open(out_path, 'w') as f:
			f.write(new_line)
		print(f"Updated {out_path} with: {new_line.strip()}")

Updated /Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/annotation/augmented/stage_5/stage_5_perm_2_case_render_2_rot140.txt with: 5 0.5634210526315789 0.3696814404432133 0.44655124653739614 0.265595567867036
Updated /Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/annotation/augmented/stage_5/stage_5_perm_1_case_render_5_rot160.txt with: 5 0.4941641337386018 0.48010638297872343 0.4624012158054711 0.35914893617021276
Updated /Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/annotation/augmented/stage_5/stage_5_perm_3_case_render_1_rot300.txt with: 5 0.34924285714285713 0.4599142857142857 0.4334142857142857 0.2785714285714286
Updated /Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/annotation/augmented/stage_5/stage_5_perm_2_case_render_9_rot160.txt with: 5 0.3196048632218844 0.5630699088145897 0.4624012158054711 0.35914893617021276
Updated /Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/annotation/augmente

# Brightness

In [22]:
def adjust_brightness_and_copy_annotation(image_path, annotation_path, out_image_path, out_annotation_path, factor):
	img = cv2.imread(image_path)
	if img is None:
		print("Failed to read image:", image_path)
		return
	# Adjust brightness/darkness using cv2.convertScaleAbs.
	adjusted_img = cv2.convertScaleAbs(img, alpha=factor, beta=0)
	cv2.imwrite(out_image_path, adjusted_img)
	
	# Copy the annotation unchanged.
	if os.path.exists(annotation_path):
		with open(annotation_path, 'r') as f:
			content = f.read()
		with open(out_annotation_path, 'w') as f:
			f.write(content)

	stages = [f"stage_{i}" for i in N_STAGES]
	# Define brightness augmentation factors.
	brightness_aug = {
		"bright125": 1.5,
		"dark075": 0.5,
	}

for stage in stages:
	in_image_folder = os.path.join(base_dir_images, stage)
	in_annotation_folder = os.path.join(base_dir_annotations, stage)
	out_image_folder = os.path.join(out_base_images, stage)
	out_annotation_folder = os.path.join(out_base_annotations, stage)
	os.makedirs(out_image_folder, exist_ok=True)
	os.makedirs(out_annotation_folder, exist_ok=True)
	
	# Cache the list of original image files (skip those already augmented)
	image_files = [f for f in os.listdir(in_image_folder)
						if f.lower().endswith(".jpg") and "_bright" not in f and "_dark" not in f]
	
	for filename in image_files:
		image_path = os.path.join(in_image_folder, filename)
		base_filename = os.path.splitext(filename)[0]
		annotation_filename = base_filename + ".txt"
		annotation_path = os.path.join(in_annotation_folder, annotation_filename)
				
		# Perform brightness/darkness augmentations.
		for tag, factor in brightness_aug.items():
			out_image_filename = f"{base_filename}_{tag}.jpg"
			out_annotation_filename = f"{base_filename}_{tag}.txt"
			out_image_path = os.path.join(out_image_folder, out_image_filename)
			out_annotation_path = os.path.join(out_annotation_folder, out_annotation_filename)
			adjust_brightness_and_copy_annotation(image_path, annotation_path, out_image_path, out_annotation_path, factor)
			print(f"Processed brightness augmentation: {out_image_path} with factor {factor}")


# obscure

For each image in the base directories, read the corresponding annotation file,
apply the obscure augmentation by drawing a random, smaller rectangle within each bounding box,
and then save the resulting image and a copy of the annotation file in the output directories.

In [55]:
def obscure_object_in_image(image, annotation_path):
	"""
	For each bounding box (in YOLO format) in the given annotation file,
	draw a randomly sized and rotated rectangle inside the bounding box to obscure it.
	"""
	H, W = image.shape[:2]
	if not os.path.exists(annotation_path):
		return image

	with open(annotation_path, 'r') as f:
		lines = f.readlines()

	for line in lines:
		parts = line.strip().split()
		if len(parts) != 5:
			continue
		cls, cx, cy, bw, bh = parts
		cx, cy, bw, bh = float(cx), float(cy), float(bw), float(bh)
		
		# Calculate bounding box pixel coordinates.
		box_w = bw * W
		box_h = bh * H
		box_x1 = cx * W - box_w / 2
		box_y1 = cy * H - box_h / 2
		box_x2 = box_x1 + box_w
		box_y2 = box_y1 + box_h

		# Determine random scale factors for the inner (obscuring) rectangle.
		scale_w = random.uniform(0.1, 0.4)
		scale_h = random.uniform(0.1, 0.4)
		rect_w = box_w * scale_w
		rect_h = box_h * scale_h

		# Choose a random center for the inner rectangle ensuring it fits within the box.
		min_cx = box_x1 + rect_w / 2
		max_cx = box_x2 - rect_w / 2
		min_cy = box_y1 + rect_h / 2
		max_cy = box_y2 - rect_h / 2
		if max_cx < min_cx or max_cy < min_cy:
			rect_center_x = (box_x1 + box_x2) / 2
			rect_center_y = (box_y1 + box_y2) / 2
		else:
			rect_center_x = random.uniform(min_cx, max_cx)
			rect_center_y = random.uniform(min_cy, max_cy)

		# Determine a random rotation angle.
		angle = random.uniform(0, 360)

		# Create the rotated rectangle and get its corner points.
		rect = ((rect_center_x, rect_center_y), (rect_w, rect_h), angle)
		box_points = cv2.boxPoints(rect)
		box_points = box_points.astype(np.int32)

		# Draw a filled rectangle (using black color to obscure).
		cv2.fillPoly(image, [box_points], (0, 0, 0))
		
	return image


stages = [f"stage_{i}" for i in range(8)]

for stage in stages:
	in_image_folder = os.path.join(base_dir_images, stage)
	in_annotation_folder = os.path.join(base_dir_annotations, stage)
	out_image_folder = os.path.join(out_base_images, stage)
	out_annotation_folder = os.path.join(out_base_annotations, stage)
	os.makedirs(out_image_folder, exist_ok=True)
	os.makedirs(out_annotation_folder, exist_ok=True)
	
	# Cache the list of original image files (skip those already augmented).
	image_files = [f for f in os.listdir(in_image_folder)
						if f.lower().endswith(".jpg") and "_obscure" not in f]
	
	for filename in image_files:
		image_path = os.path.join(in_image_folder, filename)
		base_filename = os.path.splitext(filename)[0]
		annotation_filename = base_filename + ".txt"
		annotation_path = os.path.join(in_annotation_folder, annotation_filename)
		
		img = cv2.imread(image_path)
		if img is None:
			print("Failed to read image:", image_path)
			continue

		# Obscure objects in the image using their bounding boxes.
		obscured_img = obscure_object_in_image(img, annotation_path)
		out_image_filename = f"{base_filename}_obscure.jpg"
		out_image_path = os.path.join(out_image_folder, out_image_filename)
		cv2.imwrite(out_image_path, obscured_img)
		
		# Copy annotation unchanged.
		if os.path.exists(annotation_path):
			with open(annotation_path, 'r') as f:
				content = f.read()
			out_annotation_path = os.path.join(out_annotation_folder, f"{base_filename}_obscure.txt")
			with open(out_annotation_path, 'w') as f:
				f.write(content)
		print(f"Processed obscure augmentation: {out_image_path}")


In [56]:
augment_obscure()

Processed obscure augmentation: /Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/images/augmented/stage_0/stage_0_case_render_4_rot360_dark075_obscure.jpg
Processed obscure augmentation: /Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/images/augmented/stage_0/stage_0_case_render_1_rot140_obscure.jpg
Processed obscure augmentation: /Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/images/augmented/stage_0/stage_0_case_render_7_rot140_dark075_obscure.jpg
Processed obscure augmentation: /Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/images/augmented/stage_0/stage_0_case_render_8_rot100_bright125_obscure.jpg
Processed obscure augmentation: /Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/images/augmented/stage_0/stage_0_case_render_3_rot240_obscure.jpg
Processed obscure augmentation: /Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/images/augmented/stage_0/stage_0_case_render_8_rot260_obscure.

# Visualize

In [ ]:
import matplotlib.pyplot as plt

def show_image_with_bbox(filename, bbox):
	"""
	Display an image with a bounding box drawn on it.

	Parameters:
	- filename: str, path to the image file.
	- bbox: tuple of (class_id, x_center, y_center, width, height) in YOLO format (all normalized).
	"""
	# Load the image
	image = cv2.imread(filename)
	if image is None:
		print(f"Error: Unable to load image at {filename}")
		return

	# Get image dimensions (height, width)
	h, w, _ = image.shape

	# Convert YOLO normalized coordinates to absolute pixel values
	class_id, x_center, y_center, box_width, box_height = bbox
	x_center_pixel = x_center * w
	y_center_pixel = y_center * h
	box_width_pixel = box_width * w
	box_height_pixel = box_height * h

	# Calculate top-left and bottom-right coordinates of the bounding box
	x1 = int(x_center_pixel - box_width_pixel / 2)
	y1 = int(y_center_pixel - box_height_pixel / 2)
	x2 = int(x_center_pixel + box_width_pixel / 2)
	y2 = int(y_center_pixel + box_height_pixel / 2)

	# Convert image color from BGR (OpenCV default) to RGB for matplotlib
	image_rgb = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)

	# Draw the bounding box (red color, thickness 2)
	cv2.rectangle(image_rgb, (x1, y1), (x2, y2), (255, 0, 0), 2)

	# Optionally add the class id as text above the bounding box
	label = str(int(class_id))
	cv2.putText(image_rgb, label, (x1, y1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (255, 0, 0), 2)

	# Display the image with matplotlib
	plt.figure(figsize=(8, 8))
	plt.imshow(image_rgb)
	plt.axis('off')
	plt.title("Image with Bounding Box")
	plt.show()

# Example usage
# 0.173398437
if __name__ == "__main__":
	image_filename = "/Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/images/augmented/stage_0/stage_0_case_render_4_rot20.jpg"  # Replace with your image file path
	bounding_box_filename = "/Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/annotation/augmented/stage_0/stage_0_case_render_4_rot20.txt"
	for stage in os.listdir("/Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/images/augmented"):
		if stage != "stage_7":
			continue
		for filename in os.listdir(os.path.join("/Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/images/augmented", stage)):
			if filename.endswith(".jpg"):
				image_filename = os.path.join("/Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/images/augmented", stage, filename)
				bounding_box_filename = os.path.join("/Users/georgye/Documents/repos/ethz/dslab25/training/vacuum_pump/annotation/augmented", stage, filename.replace(".jpg", ".txt"))
				with open(bounding_box_filename, 'r') as f:
					bbox_info = f.read().strip().split()
					bbox_info = (0, float(bbox_info[1]), float(bbox_info[2]), float(bbox_info[3]), float(bbox_info[4]))
					print(bounding_box_filename)
					show_image_with_bbox(image_filename, bbox_info)

# 1: x 0.317216797 0.670823568 0.5 0.51
# 2: x 0.490615234 0.670823568 0.5 0.51
# 3: x 0.664013671 0.670823568 0.5 0.51
# 4: x 0.317216797 0.497425131 0.5 0.51
# 5: x 0.490615234 0.497425131 0.5 0.51
# 6: x 0.664013671 0.497425131 0.5 0.51
# 7: x 0.317216797 0.324026694 0.5 0.51
# 8: x 0.490615234 0.324026694 0.5 0.51
# 9: x 0.664013671 0.324026694 0.5 0.51



In [ ]:
import os
import re

# Mapping for each render number to the corresponding values.
# These strings include the values separated by spaces.
render_mapping = {
	'1': "0.317216797 0.670823568 0.5 0.51",
	'2': "0.490615234 0.670823568 0.5 0.51",
	'3': "0.664013671 0.670823568 0.5 0.51",
	'4': "0.317216797 0.497425131 0.5 0.51",
	'5': "0.490615234 0.497425131 0.5 0.51",
	'6': "0.664013671 0.497425131 0.5 0.51",
	'7': "0.317216797 0.324026694 0.5 0.51",
	'8': "0.490615234 0.324026694 0.5 0.51",
	'9': "0.664013671 0.324026694 0.5 0.51"
}

def process_files():
	# Assume the script is run from the base directory.
	# Define the path to the 'anno/new' folder.
	# base_dir = os.getcwd()
	base_dir = "/Users/georgye/Documents/repos/ethz/dslab25"
	anno_new_dir = os.path.join(base_dir, "anno", "new")

	if not os.path.exists(anno_new_dir):
		print(f"Directory not found: {anno_new_dir}")
		return

	# Iterate over items in anno/new. We expect folders like stage_0, stage_1, ..., stage_7.
	for stage_folder in os.listdir(anno_new_dir):
		# Use a regex to confirm folder names of the form stage_<number>
		if not re.match(r'^stage_\d+$', stage_folder):
			continue

		stage_path = os.path.join(anno_new_dir, stage_folder)
		if not os.path.isdir(stage_path):
			continue

		# Process each file in the stage folder.
		for filename in os.listdir(stage_path):
			# Look for filenames that end with _render_<digit>.txt
			match = re.search(r'_render_([1-9])\.txt$', filename)
			if not match:
				continue

			render_number = match.group(1)
			# Build the content line: replace the "x" with the stage folder's name.
			content_line = f"{stage_folder.replace('stage_', '')} {render_mapping[render_number]}"
			file_path = os.path.join(stage_path, filename)

			try:
				with open(file_path, 'w') as file:
					file.write(content_line)
				print(f"Updated {file_path} with: {content_line}")
			except Exception as e:
				print(f"Failed to update {file_path}: {e}")

if __name__ == "__main__":
	process_files()


Updated /Users/georgye/Documents/repos/ethz/dslab25/anno/new/stage_5/stage_5_perm_5_case_render_9.txt with: 5 0.664013671 0.324026694 0.5 0.51
Updated /Users/georgye/Documents/repos/ethz/dslab25/anno/new/stage_5/stage_5_perm_5_case_render_8.txt with: 5 0.490615234 0.324026694 0.5 0.51
Updated /Users/georgye/Documents/repos/ethz/dslab25/anno/new/stage_5/stage_5_perm_1_case_render_9.txt with: 5 0.664013671 0.324026694 0.5 0.51
Updated /Users/georgye/Documents/repos/ethz/dslab25/anno/new/stage_5/stage_5_perm_1_case_render_8.txt with: 5 0.490615234 0.324026694 0.5 0.51
Updated /Users/georgye/Documents/repos/ethz/dslab25/anno/new/stage_5/stage_5_perm_4_case_render_9.txt with: 5 0.664013671 0.324026694 0.5 0.51
Updated /Users/georgye/Documents/repos/ethz/dslab25/anno/new/stage_5/stage_5_perm_4_case_render_8.txt with: 5 0.490615234 0.324026694 0.5 0.51
Updated /Users/georgye/Documents/repos/ethz/dslab25/anno/new/stage_5/stage_5_perm_2_case_render_9.txt with: 5 0.664013671 0.324026694 0.5 0.51

# Rename stuff from roboflow

In [ ]:
import os
import re

def rename_files_in_folder(folder_path):
	pattern = re.compile(r"(.*)_jpg\.rf\.[a-f0-9]+\.jpg$")

	for filename in os.listdir(folder_path):
		if filename.endswith(".txt"):
			match = pattern.match(filename)
			if match:
				new_filename = f"{match.group(1)}.txt"
				old_path = os.path.join(folder_path, filename)
				new_path = os.path.join(folder_path, new_filename)
				os.rename(old_path, new_path)
				print(f"Renamed: {filename} -> {new_filename}")

# Example usage
folder = "/Users/georgye/Documents/repos/ethz/dslab25/obj_detection/preprocessing/stage_0/images"
rename_files_in_folder(folder)